In [4]:
import os
import shutil
import zipfile
from pathlib import Path
import pandas as pd
from tqdm import tqdm

In [2]:

root_dir = r'Y:\ZHL\isds\PS\task0528'
hk_dir = os.path.join(root_dir, 'HKIsland')
kl_dir = os.path.join(root_dir, 'Kowloon')
merge_dir = os.path.join(root_dir, 'merge_dir')
merge_dir_local = r'E:\data\202502_signboard\PS\20250528'
timestamp_gap_num = 158116921

In [ ]:
def uzip_dirs(input_dir):
    sub_dirs = os.listdir(input_dir)
    for sub_name in sub_dirs:
        sub_dir = os.path.join(input_dir, sub_name)
        zip_path = os.path.join(sub_dir, 'rectified_image.zip')
        if not os.path.exists(zip_path):
            print(f'{zip_path} not exists')
        else:
            print(f'{zip_path} unzip...')
            with zipfile.ZipFile(zip_path, 'r') as zip_ref:
                zip_ref.extractall(zip_path.replace('.zip', ''))
            print(f'{zip_path} done\n')

In [ ]:
uzip_dirs(hk_dir)

In [ ]:
uzip_dirs(kl_dir)

In [ ]:
def data_check(input_dir):
    sub_dirs = os.listdir(input_dir)
    for sub_name in sub_dirs:
        sub_dir = os.path.join(input_dir, sub_name)
        gps_path = os.path.join(sub_dir, 'gps_data.txt')
        images_dir = os.path.join(sub_dir, 'rectified_image', 'rectified_image')
        df = pd.read_csv(gps_path, sep=' ')
        print(f'{sub_name} with {len(df)} gps rows, {len(os.listdir(images_dir))} images')

In [ ]:
data_check(hk_dir)
data_check(kl_dir)

In [ ]:
from img_preprocess import select_img
from deduplication_demo import filter_deduplication

def process_dirs(input_dir):
    sub_dirs = os.listdir(input_dir)
    for sub_name in sub_dirs:
        sub_dir = os.path.join(input_dir, sub_name)
        image_dir_src = os.path.join(sub_dir, 'rectified_image', 'rectified_image')
        if not os.path.exists(image_dir_src):
            print(f'{image_dir_src} not exists')
        else:
            print(f'{image_dir_src} selecting...')
            image_dir_select = os.path.join(sub_dir, 'rectified_image_select')
            select_img(image_dir_src, image_dir_select)
            print(f'{image_dir_select} filtering...')
            image_dir_filter = os.path.join(sub_dir, 'rectified_image_filter')
            filter_deduplication(image_dir_select, image_dir_filter)
            print(f'{image_dir_filter} done\n')

In [ ]:
process_dirs(hk_dir)

In [ ]:
process_dirs(kl_dir)

In [ ]:
def img_merge(input_dir, output_dir):
    sub_dirs = os.listdir(input_dir)
    for sub_name in sub_dirs:
        sub_dir = os.path.join(input_dir, sub_name)
        image_dir_src = os.path.join(sub_dir, 'rectified_image_filter')
        if not os.path.exists(image_dir_src):
            print(f'{image_dir_src} not exists')
        else:
            img_list = os.listdir(image_dir_src)
            for img_name in tqdm(img_list):
                img_path_src = os.path.join(image_dir_src, img_name)
                img_path_dst = os.path.join(output_dir, img_name)
                shutil.copyfile(img_path_src, img_path_dst)
    


In [ ]:
img_merge(hk_dir, merge_dir)

In [ ]:
img_merge(kl_dir, merge_dir)

In [5]:
def get_gps(input_dir):
    dfs = []
    sub_dirs = os.listdir(input_dir)
    for sub_name in sub_dirs:
        sub_dir = os.path.join(input_dir, sub_name)
        gps_path = os.path.join(sub_dir, 'gps_data.txt')
        images_dir = os.path.join(sub_dir, 'rectified_image', 'rectified_image')
        if not os.path.exists(gps_path):
            print(f'{gps_path} not exists')
        else:
            df = pd.read_csv(gps_path, sep=' ', header=0)
            dfs.append(df)
    return dfs


In [6]:
dfs1 = get_gps(hk_dir)
dfs2 = get_gps(kl_dir)
dfs = pd.concat(dfs1+dfs2, axis=0)

In [7]:
dfs['timestamp_jpg'] = dfs['#timestamp']-timestamp_gap_num
dfs['with_jpg'] = False

In [8]:
image_list = os.listdir(merge_dir)
for img_name in tqdm(image_list):
    if not img_name.endswith('.jpg'):
        continue
    img_timestamp = int(float(Path(img_name).stem))
    if img_timestamp not in dfs['timestamp_jpg'].values:
        print(f'{img_timestamp} not exists')
    else:
        dfs.loc[dfs['timestamp_jpg'] == img_timestamp, 'with_jpg'] = True
dfs_with_jpg = dfs[dfs['with_jpg']==True]

100%|██████████| 3387/3387 [00:00<00:00, 7303.77it/s]


In [9]:
import pandas as pd
from geopy.distance import great_circle

# 按时间排序
dfs_with_jpg['timestamp'] = dfs_with_jpg['timestamp_jpg']
df = dfs_with_jpg.sort_values(by='timestamp')

# 分割轨迹（示例阈值：5分钟或1公里）
df['trajectory_id'] = 0
current_id = 0
prev_time = df.iloc[0]['timestamp']
prev_point = (df.iloc[0]['latitude'], df.iloc[0]['longitude'])

for i in range(1, len(df)):
    curr_time = df.iloc[i]['timestamp']
    curr_point = (df.iloc[i]['latitude'], df.iloc[i]['longitude'])
    time_diff = (curr_time - prev_time) / 60  # 分钟
    distance = great_circle(prev_point, curr_point).meters
    
    if time_diff > 5 or distance > 10000:
        current_id += 1
    df.at[i, 'trajectory_id'] = current_id
    prev_time, prev_point = curr_time, curr_point

C:\Users\USER\AppData\Local\Temp\ipykernel_28260\1297874373.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dfs_with_jpg['timestamp'] = dfs_with_jpg['timestamp_jpg']


In [10]:
from geopy.geocoders import Nominatim

geolocator = Nominatim(user_agent="geoapi")

def get_street(row):
    try:
        location = geolocator.reverse((row['latitude'], row['longitude']), exactly_one=True)
        address = location.raw.get('address', {})
        return address.get('road') or address.get('street')
    except:
        return None

df['street'] = df.apply(get_street, axis=1)
df['main_street'] = df.groupby('trajectory_id')['street'].transform(lambda x: x.mode()[0])

KeyError: 0

In [ ]:
from shapely.geometry import LineString
from scipy.spatial.distance import directed_hausdorff
import numpy as np

# 生成 LineString 轨迹
def create_linestring(group):
    coords = list(zip(group['longitude'], group['latitude']))
    return LineString(coords)

df['linestring'] = df.groupby('trajectory_id')['linestring'].transform(create_linestring)

# 按街道分组去重
keep_trajectories = set()

for street, group in df.groupby('main_street'):
    trajectories = []
    for traj_id in group['trajectory_id'].unique():
        traj_points = group[group['trajectory_id'] == traj_id][['longitude', 'latitude']].values
        traj_line = LineString(traj_points)
        trajectories.append((traj_id, traj_line))
    
    # 比较轨迹相似性（Hausdorff 距离）
    to_remove = set()
    for i in range(len(trajectories)):
        if i in to_remove:
            continue
        for j in range(i+1, len(trajectories)):
            dist = max(
                directed_hausdorff(trajectories[i][1].coords, trajectories[j][1].coords)[0],
                directed_hausdorff(trajectories[j][1].coords, trajectories[i][1].coords)[0]
            )
            if dist < 0.0001:  # 阈值（单位：度，需转换为米）
                to_remove.add(j)
    
    # 保留未被移除的轨迹
    for idx, (traj_id, _) in enumerate(trajectories):
        if idx not in to_remove:
            keep_trajectories.add(traj_id)

In [ ]:
result_df = df[df['trajectory_id'].isin(keep_trajectories)]

In [11]:
import folium

# 假设 df 是您的轨迹点 DataFrame
df = dfs_with_jpg

# 创建地图（中心点可选）
m = folium.Map(location=[df['latitude'].mean(), df['longitude'].mean()], zoom_start=15)

# 添加轨迹点（每个点作为一个 Marker）
for i in range(len(df)):
    folium.Marker(
        location=(df.iloc[i]['latitude'], df.iloc[i]['longitude']),
        popup=f"Timestamp: {df.iloc[i]['#timestamp']}",  # 可选：显示时间戳
        icon=folium.Icon(color="blue", icon="info-sign")  # 可选：自定义图标
    ).add_to(m)

# 保存地图为 HTML 文件
m.save("trajectory_points_map.html")

In [12]:
m